In [1]:
#ライブラリインポート
import re
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_squared_log_error
import lightgbm as lgb
import scipy as sp
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Ridge, RidgeCV, ElasticNet, LassoCV, LassoLarsCV
from sklearn.model_selection import cross_val_score
import xgboost as xgb
from xgboost.sklearn import XGBRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import KFold
from sklearn.externals import joblib

# Pandasでの表示が省略されないように設定
pd.set_option("max_columns", 1000)
pd.set_option('max_rows',1000)
pd.set_option('max_info_columns',1000)

# Jupyterの枠を広げる
from IPython.core.display import display, HTML
display(HTML("<style>.container{width:96%!important;}</style>"))

In [2]:
#全データ読み込み
total_df = pd.read_csv("total_df.csv",index_col=0)
train_df = pd.read_csv("train_df.csv",index_col=0)
test_df = pd.read_csv("test_df.csv",index_col=0)

smpsb_df = pd.read_csv("Data/sample_submit.csv", header=None)

In [3]:
# 今回は時系列データなので、ある期間との前後でデータを分ける
# 2015年までのデータを訓練データ
# 2016年のデータを検証用データにする
all_train_X = train_df.query("match_date_year <= 2016").drop(["id", "attendance"], axis=1)
all_train_y = train_df.query("match_date_year <= 2016")["attendance"]

train_X = train_df.query("match_date_year <= 2015").drop(["id", "attendance"], axis=1)
train_y = train_df.query("match_date_year <= 2015")["attendance"]

val_X = train_df.query("match_date_year == 2016").drop(["id", "attendance"], axis=1)
val_y = train_df.query("match_date_year == 2016")["attendance"]

test_X = test_df.drop(["id"], axis=1)

In [7]:
#全データで学習
# GridWSerchの動かすパラメータを明示的に表示
params = {'colsample_bytree':[0.73,0.75,0.76,0.77],
          'learning_rate': [0.065,0.068,0.069,0.070],
          'max_depth':[6,7,8,9,10],
          'min_child_weight':[2.0,2.1,2.2,2.3],
          'subsample':[0.80,0.84,0.85,0.87]
          }

kf_10 = KFold(n_splits=10,random_state=0)
# モデルにインスタンス生成
mod = xgb.XGBRegressor(seed=0)
# ハイパーパラメータ探索
cv = GridSearchCV(mod, params, cv =10, scoring= "neg_mean_squared_log_error", n_jobs =-1,verbose=10)

# 予測モデルを作成
cv.fit(all_train_X ,all_train_y)

Fitting 10 folds for each of 1280 candidates, totalling 12800 fits
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8 
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8, score=-0.0741230214412847, total=   0.9s


[Parallel(n_jobs=-1)]: Done   2 tasks      | elapsed:    1.0s


[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.05151143123754488, total=   0.9s
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84 
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.07298102686269556, total=   0.9s
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8, score=-0.05031529648656868, total=   0.9s
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.8, score=-0.04041183991538952, total=   0.9s
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84 
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.05362730488511807, t

[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:    1.9s
[Parallel(n_jobs=-1)]: Done  16 tasks      | elapsed:    2.0s


[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.038884355793881324, total=   0.9s
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.85 
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.05143988265960679, total=   0.9s
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.04894021489522166, total=   0.9s
[CV]  colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.84, score=-0.04047317161494489, total=   0.9s
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.85 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.85 
[CV] colsample_bytree=0.73, learning_rate=0.065, max_depth=6, min_child_weight=2.0, subsample=0.85 
[CV]  colsample_bytree=0.73

...

[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.84 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.8, score=-0.046970047855720155, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.84 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.8, score=-0.03818785348035696, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.84 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.8, score=-0.04986720235237603, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.84 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.8, score=-0.0375750440809849, total=   1.8s
[CV] colsample_bytree=0.77, lear

[Parallel(n_jobs=-1)]: Done 12784 tasks      | elapsed: 37.4min


[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.85, score=-0.049262603606884815, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.87 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.85, score=-0.039738268224037775, total=   1.8s
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.87, score=-0.0688366841825511, total=   1.8s
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.85, score=-0.04034541688615591, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.87 
[CV]  colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3, subsample=0.85, score=-0.048570566111527214, total=   1.8s
[CV] colsample_bytree=0.77, learning_rate=0.07, max_depth=10, min_child_weight=2.3,

[Parallel(n_jobs=-1)]: Done 12800 out of 12800 | elapsed: 37.4min finished


GridSearchCV(cv=10, error_score='raise',
       estimator=XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=3, min_child_weight=1, missing=None, n_estimators=100,
       n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=0, silent=True,
       subsample=1),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'colsample_bytree': [0.73, 0.75, 0.76, 0.77], 'learning_rate': [0.065, 0.068, 0.069, 0.07], 'max_depth': [6, 7, 8, 9, 10], 'min_child_weight': [2.0, 2.1, 2.2, 2.3], 'subsample': [0.8, 0.84, 0.85, 0.87]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='neg_mean_squared_log_error', verbose=10)

In [8]:
# bestパラメータ確認
cv.best_params_

{'colsample_bytree': 0.75,
 'learning_rate': 0.07,
 'max_depth': 9,
 'min_child_weight': 2.1,
 'subsample': 0.85}

In [9]:
#全データに対するRMSLE (Root Mean Squared Logarithmic Error:対数平方平均二乗誤差) :　前回のスコア→0.21492959647963436
np.sqrt(cv.best_score_*(-1))

0.21467331598568506

In [4]:
# 全データに対して改めて学習
# LightGBM parameters
params2 = {
        'max_depth': [7,8,9,10],
        'learning_rate': [0.092,0.094,0.095,0.096],
        'colsample_bytree':[0.79,0.80,0.82,0.84],
        'min_child_weight':[1.0,1,1,1.2,1.3],
        'subsample':[0.25,0.28,0.30,0.32]
    
}
kf_10 = KFold(n_splits=10,random_state=0)

# モデルにインスタンス生成
gbm = lgb.LGBMRegressor(seed=0)
# ハイパーパラメータ探索
gbm_cv = GridSearchCV(gbm,params2,cv = kf_10, scoring= "neg_mean_squared_log_error", n_jobs =-1,verbose=10)

# 予測モデルを作成
gbm_cv.fit(all_train_X ,all_train_y)

Fitting 10 folds for each of 1280 candidates, totalling 12800 fits
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.0724912035544935, total

[Parallel(n_jobs=-1)]: Done   2 tasks      | elapsed:    2.2s


[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.03747794578568937, total=   2.3s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.05074688664146499, total=   2.3s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.04709106565706221, total=   2.4s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.03768441673969127, total=   2.2s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28 
[CV]  colsample_bytree=0.79,

[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:    4.4s


[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28, score=-0.04227727790363862, total=   2.2s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.25, score=-0.0496784615799695, total=   2.4s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.3 
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28, score=-0.048708317155870595, total=   2.4s
[CV]  colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.28, score=-0.04875915409218814, total=   2.3s
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.3 
[CV] colsample_bytree=0.79, learning_rate=0.092, max_depth=7, min_child_weight=1.0, subsample=0.3 
[CV]  colsample_bytree=0.79, le

...

[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.25 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.25, score=-0.04080087299231081, total=   2.3s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.28 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.25, score=-0.047594872480273304, total=   2.5s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.28 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.25, score=-0.04945128574458873, total=   2.3s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.28 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.25, score=-0.036172835031633106, total=   2.3s
[CV] colsample_byt

[Parallel(n_jobs=-1)]: Done 12784 tasks      | elapsed: 63.3min


[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.3, score=-0.03690779198967188, total=   2.4s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.32 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.3, score=-0.036172835031633106, total=   2.4s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.32 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.3, score=-0.04789754192667165, total=   2.6s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.32 
[CV]  colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.3, score=-0.051102121456838734, total=   2.5s
[CV] colsample_bytree=0.84, learning_rate=0.096, max_depth=10, min_child_weight=1.3, subsample=0.32 
[CV]  colsample_bytree

[Parallel(n_jobs=-1)]: Done 12800 out of 12800 | elapsed: 63.4min finished


GridSearchCV(cv=KFold(n_splits=10, random_state=0, shuffle=False),
       error_score='raise',
       estimator=LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
       learning_rate=0.1, max_depth=-1, min_child_samples=20,
       min_child_weight=0.001, min_split_gain=0.0, n_estimators=100,
       n_jobs=-1, num_leaves=31, objective=None, random_state=None,
       reg_alpha=0.0, reg_lambda=0.0, seed=0, silent=True, subsample=1.0,
       subsample_for_bin=200000, subsample_freq=0),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_depth': [7, 8, 9, 10], 'learning_rate': [0.092, 0.094, 0.095, 0.096], 'colsample_bytree': [0.79, 0.8, 0.82, 0.84], 'min_child_weight': [1.0, 1, 1, 1.2, 1.3], 'subsample': [0.25, 0.28, 0.3, 0.32]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='neg_mean_squared_log_error', verbose=10)

In [5]:
# bestパラメータ確認
gbm_cv.best_params_

{'colsample_bytree': 0.82,
 'learning_rate': 0.096,
 'max_depth': 10,
 'min_child_weight': 1.0,
 'subsample': 0.25}

In [6]:
#全データに対するRMSLE (Root Mean Squared Logarithmic Error:対数平方平均二乗誤差) :　前回のスコア→0.23008283859317474
np.sqrt(gbm_cv.best_score_*(-1))

0.21466417971759558

In [10]:
filename = "Xgboost.sav"
joblib.dump(cv, filename)

['11_22_Xgboost.sav']

In [11]:
filename2 = "LightGBM.sav"
joblib.dump(gbm_cv, filename2)

['11_22_LightGBM.sav']

In [12]:
pred1 = cv.predict(test_X)

In [13]:
pred1

array([42718.004 , 15062.111 , 23199.662 , 18179.932 , 19119.6   ,
       15131.928 , 23486.523 , 13647.114 , 26301.574 , 48315.48  ,
       13050.336 , 16582.664 , 23973.777 , 12006.98  , 18372.963 ,
       12157.353 , 13019.745 , 19437.69  , 12823.292 , 14955.792 ,
       22510.06  , 15916.888 ,  9200.66  , 10571.517 , 20564.818 ,
       14467.53  , 24591.904 , 13475.801 , 16443.979 ,  9387.486 ,
       15585.815 , 10785.181 , 10215.692 , 18125.156 , 28575.395 ,
       33098.086 , 13417.708 , 20323.432 , 13158.357 , 19141.293 ,
       13383.307 , 19715.2   , 21057.172 , 12249.684 , 10408.479 ,
       17416.062 , 25945.129 , 16260.712 , 20326.574 ,  8357.112 ,
        8890.338 ,  8503.637 , 13474.267 , 19561.404 , 17644.52  ,
       11831.431 , 14434.762 , 32811.17  , 36971.547 , 10825.821 ,
       17987.047 , 15875.285 , 16806.668 , 15819.118 , 21244.332 ,
       34607.86  , 10619.038 , 12757.04  , 16468.393 , 11473.11  ,
       21424.818 , 13815.8   , 13243.13  , 24193.16  , 14108.1

In [14]:
pred2 = gbm_cv.predict(test_X)

In [15]:
pred2

array([43805.43990971, 16462.97299712, 23829.19769005, 17281.88921406,
       19803.71636891, 14573.31548652, 23216.27986432, 13426.40804237,
       28037.3190397 , 48828.21785829, 13973.08333495, 15865.04199881,
       24448.04812962, 12490.40334899, 16508.43896029, 12114.26521949,
       14051.57685185, 18512.49528528, 14300.23016372, 13524.3157453 ,
       24447.10860721, 14621.5403156 ,  9591.6544478 , 11361.12807581,
       21363.13435233, 16030.96786298, 24547.34857607, 13602.13831979,
       15988.28471551,  9621.19250291, 15418.19724621, 10130.86313315,
        9325.1048243 , 17289.63473227, 26025.72603177, 32829.36294727,
       14129.15922214, 21134.64484335, 11830.03146782, 17188.05096804,
       12288.75436158, 17472.69404152, 20118.50589371, 11018.62274544,
       10509.17189327, 17294.36982465, 24829.12610308, 15616.58788653,
       18899.93028255,  7899.21845937,  8280.06465182,  8984.50002106,
       16088.79099046, 19133.44544927, 16937.50850407, 10975.53589569,
      

In [17]:
#予測結果をアンサンブル
pred = np.average(np.array([pred1,pred2]),axis=0,weights=[0.55,0.45])
smpsb_df.iloc[:len(test_X), 1]= pred
smpsb_df[1].head()


0    43207.350108
1    15692.499079
2    23482.953121
3    17775.812549
4    19427.452151
Name: 1, dtype: float64